<a href="https://colab.research.google.com/github/Hasnafi/Drowsiness-Detection-using-CNN/blob/main/Drowsiness_Detection_using_CNN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import numpy as np
import os
import cv2

from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from keras.models import Sequential
from keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout

Importer le dataset

In [ ]:
# Load the dataset and preprocess it
data_dir = "./dataset"
closed_dir = os.path.join(data_dir,"Closed_Eyes")
open_dir = os.path.join(data_dir, "Open_Eyes")


Data Processing

In [ ]:
closed_images = []
open_images = []
labels= []

# Load closed eye images
for img in os.listdir(closed_dir):
    img_path = os.path.join(closed_dir, img)
    image = cv2.imread(img_path)
    image = cv2.resize(image, (100,100)) # Resize images to a fixed size
    closed_images.append(image)
    labels.append(0) # 0 for closed eyes

# Load open eye images
for img in os.listdir(open_dir) :
    img_path = os.path.join(open_dir, img)
    image = cv2.imread(img_path)
    image= cv2.resize(image, (100,100))
    open_images.append(image)
    labels.append(1) # 1 for open eyes

# Convert lists to numpy arrays
closed_images = np.array(closed_images)
open_images= np.array(open_images)
labels = np.array(labels)

# Combine closed and open eye images
X = np.concatenate ((closed_images, open_images), axis=0)

# Normalization of the images
X = X / 255.0

Split data into two parts :


1.   testing sets
2.   training sets



In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, labels, test_size = 0.2, random_state=42)

3. Build the CNN model

In [ ]:
model = Sequential([
    Conv2D(64, (3,3), activation='relu', input_shape=(100,100,3)),  # Increased filters to 64
    MaxPooling2D((2,2)),
    Conv2D(128, (3,3), activation='relu'),  # Increased filters to 128
    MaxPooling2D((2,2)),
    Conv2D(256, (3,3), activation='relu'),  # Added another Conv2D layer with 256 filters
    MaxPooling2D((2,2)),
    Flatten(),
    Dense(256, activation='relu'),  # Increased neurons to 256
    Dropout(0.5),
    Dense(1, activation='sigmoid')
])

model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])

4. Train the model

In [ ]:
model.fit(X_train, y_train, epochs=10, batch_size=32, validation_split=0.1)

Epoch 1/10
42/42 [==============================] - 87s 2s/step - loss: 0.4091 - accuracy: 0.8042 - val_loss: 0.1049 - val_accuracy: 0.9664
Epoch 2/10
42/42 [==============================] - 81s 2s/step - loss: 0.2818 - accuracy: 0.8602 - val_loss: 0.1814 - val_accuracy: 0.9664
Epoch 3/10
42/42 [==============================] - 78s 2s/step - loss: 0.1207 - accuracy: 0.9589 - val_loss: 0.1014 - val_accuracy: 0.9799
Epoch 4/10
42/42 [==============================] - 77s 2s/step - loss: 0.0502 - accuracy: 0.9828 - val_loss: 0.0343 - val_accuracy: 0.9799
Epoch 5/10
42/42 [==============================] - 81s 2s/step - loss: 0.0448 - accuracy: 0.9895 - val_loss: 0.0233 - val_accuracy: 0.9933
Epoch 6/10
42/42 [==============================] - 75s 2s/step - loss: 0.0244 - accuracy: 0.9918 - val_loss: 0.0239 - val_accuracy: 0.9866
Epoch 7/10
42/42 [==============================] - 76s 2s/step - loss: 0.0257 - accuracy: 0.9910 - val_loss: 0.0298 - val_accuracy: 0.9799
Epoch 8/10
42/42 [==

In [ ]:
print(model.input_shape)


(None, 100, 100, 3)


Evaluation of the model, the model predicts the probability that each sample belongs to the positive class (open eyes)

In [ ]:
y_pred = model.predict(X_test)
y_pred = (y_pred > 0.5).astype(int)
accuracy = accuracy_score(y_test, y_pred)
print('Accuracy on test set :', accuracy)

12/12 [==============================] - 11s 924ms/step
Accuracy on test set : 0.9865591397849462


Save the model

In [ ]:
model.save("eye_detection.h5")

In [ ]:
import cv2
import numpy as np
import tensorflow as tf
import threading
from google.colab.patches import cv2_imshow
from IPython.display import HTML
from base64 import b64encode

# Charger votre modèle pré-entraîné pour la détection de l'état des yeux
model = tf.keras.models.load_model('eye_detection.h5')

# Fonction pour prétraiter les images des yeux pour le modèle
def preprocess_eye(eye_img):
    # S'assurer que l'image est en format RGB
    if len(eye_img.shape) == 2 or eye_img.shape[2] == 1:
        eye_img = cv2.cvtColor(eye_img, cv2.COLOR_GRAY2RGB)

    # Redimensionner pour correspondre à la taille d'entrée du modèle
    eye_img = cv2.resize(eye_img, (100, 100))

    # Normaliser entre [0, 1]
    eye_img = eye_img.astype('float32') / 255.0

    # Ajouter une dimension de lot
    eye_img = np.expand_dims(eye_img, axis=0)

    return eye_img

# Fonction pour prédire l'état des yeux
def predict_eye_state(eye_img):
    preprocessed_eye = preprocess_eye(eye_img)
    prediction = model.predict(preprocessed_eye)
    if prediction[0][0] > 0.5:  # Supposons que le modèle sort la probabilité pour 'ouvert'
        return 'open'
    else:
        return 'closed'

# Fonction pour jouer un son d'alerte
def play_alert_sound():
    playsound('videoplayback.m4a')
    print("ALERT !")

# Charger les Haar cascades pour la détection du visage et des yeux
face_cascade = cv2.CascadeClassifier(cv2.data.haarcascades + 'haarcascade_frontalface_default.xml')
eye_cascade = cv2.CascadeClassifier(cv2.data.haarcascades + 'haarcascade_eye.xml')

# Ouvrir le fichier vidéo
cap = cv2.VideoCapture('video2.mp4')

if not cap.isOpened():
    print("Error: Could not open video.")
    exit()

# Définir le codec et créer un objet VideoWriter pour enregistrer la vidéo de sortie
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter('output_video.mp4', fourcc, 20.0, (1280, 720))

closed_eyes_counter = 0  # Compteur pour les yeux fermés
closed_eyes_threshold = 5  # Seuil de cadres consécutifs pour déclencher l'alerte

while True:
    ret, frame = cap.read()
    if not ret:
        break

    # Redimensionner le cadre à la résolution cible
    target_width = 1280
    target_height = 720
    frame = cv2.resize(frame, (target_width, target_height))

    # Convertir le cadre en niveaux de gris
    gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    gray = cv2.equalizeHist(gray)

    # Détecter les visages dans le cadre
    faces = face_cascade.detectMultiScale(gray, scaleFactor=1.3, minNeighbors=5, minSize=(30, 30))

    for (x, y, w, h) in faces:
        cv2.rectangle(frame, (x, y), (x+w, y+h), (255, 0, 0), 2)
        roi_gray = gray[y:y+h, x:x+w]
        roi_color = frame[y:y+h, x:x+w]

        # Détecter les yeux dans la région du visage
        eyes = eye_cascade.detectMultiScale(roi_gray, scaleFactor=1.6, minNeighbors=3, minSize=(20, 10))

        eyes_detected = False
        for (ex, ey, ew, eh) in eyes:
            eye_img = roi_color[ey:ey+eh, ex:ex+ew]
            eye_state = predict_eye_state(eye_img)
            label = f'Eye: {eye_state}'
            cv2.rectangle(roi_color, (ex, ey), (ex+ew, ey+eh), (0, 255, 0), 2)
            cv2.putText(roi_color, label, (ex, ey - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)

            if eye_state == 'closed':
                eyes_detected = True

        if eyes_detected:
            closed_eyes_counter += 1
            if closed_eyes_counter >= 2:
                threading.Thread(target=play_alert_sound).start()
                closed_eyes_counter = 0  # Réinitialiser le compteur après l'alerte
        else:
            closed_eyes_counter = 0  # Réinitialiser si les yeux sont ouverts

    out.write(frame)

cap.release()
out.release()
cv2.destroyAllWindows()

# Fonction pour afficher la vidéo dans le notebook
def display_video(video_path):
    video_file = open(video_path, "rb").read()
    video_url = "data:video/mp4;base64," + b64encode(video_file).decode()
    return HTML(f"""<video width=1280 controls>
                      <source src="{video_url}" type="video/mp4">
                    </video>""")

# Afficher la vidéo
display_video('output_video.mp4')


1/1 [==============================] - 0s 56ms/step


Exception in thread Thread-70 (play_alert_sound):
Traceback (most recent call last):
  File "/usr/lib/python3.10/threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "/usr/lib/python3.10/threading.py", line 953, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-20-891d1905cbef>", line 40, in play_alert_sound
NameError: name 'playsound' is not defined


1/1 [==============================] - 0s 39ms/step


Exception in thread Thread-71 (play_alert_sound):
Traceback (most recent call last):
  File "/usr/lib/python3.10/threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "/usr/lib/python3.10/threading.py", line 953, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-20-891d1905cbef>", line 40, in play_alert_sound
NameError: name 'playsound' is not defined


1/1 [==============================] - 0s 104ms/step


...

Exception in thread Thread-126 (play_alert_sound):
Traceback (most recent call last):
  File "/usr/lib/python3.10/threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "/usr/lib/python3.10/threading.py", line 953, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-20-891d1905cbef>", line 40, in play_alert_sound
NameError: name 'playsound' is not defined


1/1 [==============================] - 0s 62ms/step


Exception in thread Thread-127 (play_alert_sound):
Traceback (most recent call last):
  File "/usr/lib/python3.10/threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "/usr/lib/python3.10/threading.py", line 953, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-20-891d1905cbef>", line 40, in play_alert_sound
NameError: name 'playsound' is not defined


1/1 [==============================] - 0s 37ms/step


Exception in thread Thread-128 (play_alert_sound):
Traceback (most recent call last):
  File "/usr/lib/python3.10/threading.py", line 1016, in _bootstrap_inner
    self.run()
  File "/usr/lib/python3.10/threading.py", line 953, in run
    self._target(*self._args, **self._kwargs)
  File "<ipython-input-20-891d1905cbef>", line 40, in play_alert_sound
NameError: name 'playsound' is not defined
